In [1]:
# using Pkg
# Pkg.generate("model0")

In [2]:
# using Pkg
# Pkg.add("OrdinaryDiffEq")
# Pkg.add("DifferentialEquations")
# Pkg.add("ModelingToolkit")
# Pkg.add("DataDrivenDiffEq")
# Pkg.add("LinearAlgebra")
# Pkg.add("DiffEqSensitivity")
# Pkg.add("Optim")
# Pkg.add("DiffEqFlux")
# Pkg.add("Flux")
# Pkg.add("Plots")
# Pkg.add("DataFrames")
# Pkg.add("GLM")
# Pkg.add("StatsModels")
# Pkg.add("CSV")
# Pkg.add("Interpolations")
# Pkg.add("JLD2")
# Pkg.add("Suppressor")
# Pkg.add("Distributed")
# Pkg.add("ParallelDataTransfer")
# Pkg.add("LaTeXStrings")
# Pkg.add("Statistics")
# Pkg.add("StatsBase")
# Pkg.add("TickTock")

In [3]:
println(@__DIR__)
using Pkg
# Pkg.update()
Pkg.activate(string(@__DIR__, "/model0/Project.toml"))
Pkg.status()
# Pkg.instantiate()

/home/ziyu/solow/NODE/Neural Ordinary Differential Equations for the Regression and Prediction of Macroeconomics Data under the Green Solow Model/Upload/all_countries


 Activating environment at `~/solow/NODE/Neural Ordinary Differential Equations for the Regression and Prediction of Macroeconomics Data under the Green Solow Model/Upload/all_countries/model0/Project.toml`


Project model0 v0.1.0
Status `~/solow/NODE/Neural Ordinary Differential Equations for the Regression and Prediction of Macroeconomics Data under the Green Solow Model/Upload/all_countries/model0/Project.toml`
  [336ed68f] CSV v0.8.4
  [2445eb08] DataDrivenDiffEq v0.5.5
  [a93c6f00] DataFrames v0.22.5
  [aae7a2af] DiffEqFlux v1.23.0
  [41bf760c] DiffEqSensitivity v6.33.0
  [0c46a032] DifferentialEquations v6.16.0
  [587475ba] Flux v0.11.1
  [38e38edf] GLM v1.4.0
  [a98d9a8b] Interpolations v0.13.1
  [033835bb] JLD2 v0.4.2
  [b964fa9f] LaTeXStrings v1.2.1
  [961ee093] ModelingToolkit v5.11.0
  [429524aa] Optim v1.2.4
  [1dea7af3] OrdinaryDiffEq v5.51.1
  [2dcacdae] ParallelDataTransfer v0.5.0
  [91a5bcdd] Plots v1.6.12
  [2913bbd2] StatsBase v0.33.3
  [3eaba693] StatsModels v0.6.21
  [fd094767] Suppressor v0.2.0
  [9ff05d80] TickTock v1.1.0
  [8ba89e20] Distributed 
  [37e2e46d] LinearAlgebra 
  [10745b16] Statistics 


In [4]:
# cd(@__DIR__)
# using Pkg; Pkg.activate("."); Pkg.instantiate()
using OrdinaryDiffEq, DifferentialEquations
using ModelingToolkit
using DataDrivenDiffEq
using LinearAlgebra, DiffEqSensitivity, Optim
using DiffEqFlux, Flux
using Plots
using DataFrames, GLM, StatsModels
using CSV
using Interpolations
using JLD2
using Suppressor
using Distributed
using ParallelDataTransfer
using LaTeXStrings, Statistics
using StatsBase
using TickTock
gr()

Plots.GRBackend()

# Cleaning data, getting all parameters and list of countries

In [5]:
country_list = ["Albania", "Argentina", "Australia", "Bahrain", "Bangladesh", "Benin", "Botswana", "Brazil", "Bulgaria", "Burundi", "Cameroon", "Canada", "Chile", "China", "Colombia", "Costa Rica", "Denmark", "Dominican Republic", "Ecuador", "El Salvador", "Finland", "France", "Gabon", "Ghana", "Greece", "Guatemala", "Guinea", "Honduras", "India", "Israel", "Italy", "Jamaica", "Jordan", "Kenya", "Kuwait", "Madagascar", "Malawi", "Malaysia", "Mali", "Mauritania", "Mauritius", "Mexico", "Mongolia", "Morocco", "Nepal", "Netherlands", "Niger", "Nigeria", "Norway", "Oman", "Pakistan", "Panama", "Peru", "Philippines", "Portugal", "Saudi Arabia", "Senegal", "Sierra Leone", "Singapore", "South Africa", "Spain", "Sri Lanka", "Sudan", "Sweden", "Switzerland", "Thailand", "Togo", "Tunisia", "Turkey", "Uganda", "United Kingdom", "United States", "Uruguay"]

73-element Array{String,1}:
 "Albania"
 "Argentina"
 "Australia"
 "Bahrain"
 "Bangladesh"
 "Benin"
 "Botswana"
 "Brazil"
 "Bulgaria"
 "Burundi"
 "Cameroon"
 "Canada"
 "Chile"
 ⋮
 "Sri Lanka"
 "Sudan"
 "Sweden"
 "Switzerland"
 "Thailand"
 "Togo"
 "Tunisia"
 "Turkey"
 "Uganda"
 "United Kingdom"
 "United States"
 "Uruguay"

In [6]:
paras2 = CSV.read(string(@__DIR__, "/model0_initialisation/Nelder_Mead_parameters.csv"),
    normalizenames = true, 
    DataFrame)

function get_parameters(country_input)
    country_input_underscore = replace(country_input, " " => "_")
    paras1 = CSV.read(string(@__DIR__, "/model0_initialisation/model3full/",country_input_underscore,"model3full.csv"),
        normalizenames = true, 
        DataFrame)
    set1 = Array(paras1[!,country_input_underscore]) #α,δ,gᵦ,gₐ
    set2 = values(paras2[paras2.country .== country_input,2:5])
# set2 = paras2[paras2.country == "Albania",:]
return set1, set2[!,1], set2[!,2], set2[!,3], set2[!,4]
end

get_parameters (generic function with 1 method)

Getting time series data

In [7]:
function getCleandataFrame(country)
    df_year=df[!,"Year"][2:end]
    df1=df[!,string(country,"_yt")]  #GDP
    df2=df[!,string(country,"_kt")] #capital per capita
    df3=df[!,string(country,"_srate")][2:end] # savig rate
    df6= df[!,string(country,"_et")] #population
    df4= df[!,string(country,"_nt")][2:end] #population
    df8=df6[1:end-1] .-df6[2:end]#de
    df6=df6[2:end]
    df5=df2[1:end-1] .-df2[2:end] #dk
    df2=df2[2:end]
    df7= df1[1:end-1] .-df1[2:end] # dydt
    df1=df1[2:end]
    newdf= DataFrame(Year=df_year,yt=df1, k=df2, srate=df3,nt=df4,dkdt=df5,dydt=df7,dedt=df8,et=df6)
    newdf=newdf[completecases(newdf), :]
    return newdf, df8, df5, df7
end


getCleandataFrame (generic function with 1 method)

In [8]:
df = CSV.read(string(@__DIR__, "/compileddf.csv"),
    normalizenames = true, 
    DataFrame)

function generate_data(country)
    newdf, df8, df5, df7=getCleandataFrame(country)
    years_available=size(newdf)[1]

    st = interpolate(newdf[!,"srate"], BSpline(Quadratic(Free(OnCell()))))
    nt = interpolate(newdf[!,"nt"], BSpline(Quadratic(Free(OnCell()))))
    kdata= newdf[!,"k"]
    ydata=newdf[!,"yt"]
    edata=newdf[!,"et"]
    kic= newdf[!,"k"][1]
    yic=newdf[!,"yt"][1]
    eic=newdf[!,"et"][1]
    kₜ= kdata
    yₜ = ydata
    eₜ = edata
    s = st
    n = nt
return years_available, st, nt, kdata, ydata, edata, kic, yic, eic, kₜ, yₜ, eₜ, s, n, df8, df5, df7
end

generate_data (generic function with 1 method)

Using the parameters to solve the ODEs as a coupled system. 

The ODEs are solved using TRBDF2 because the problem is stiff. The solver is robust to oscillations and massive stiffness. 

We see if training with a neural network can reduce losses

In [9]:
function generate_parameters_and_predictions(α,δ,gᵦ,gₐ,country)
    println("parameters received: ", α, ", ", δ,", ",gᵦ,", ",gₐ)
    
    
    years_available, st, nt, kdata, ydata, edata, kic, yic, eic, kₜ, yₜ, eₜ, s, n, df8, df5, df7 = generate_data(country)  
    
    function solownneqn1(du,u,p,t)
        sₜ = st(t) #savings rate
        nₜ = nt(t)
        k = u[1]
        y=u[2]
        e=u[3]
        α,δ,gᵦ,gₐ= p
        du[1] = sₜ*y-(δ+nₜ+gᵦ)*k # rate of change of kt
        du[2] = y*(gᵦ+α*du[1]/k) # rate of change of yt
        du[3] = e*(-gₐ+du[2]/y)
    return du
    end

    nntspan = (1.0e0,years_available*1.0) ## the year is hard coded, to be changed later
    nndatasize = years_available
    nntsteps = range(nntspan[1], nntspan[2], length=nndatasize)
    u0 = Float32[kic,yic,eic] ## kt initial
    nnp = [α,δ,gᵦ,gₐ]
    prob_solownneqn = ODEProblem(solownneqn1, u0, nntspan, nnp)
    pred = solve(prob_solownneqn, TRBDF2(),p=nnp, abstol=1e-4, reltol=1e-4, saveat = nntsteps)

    function predicts(θ)
        Array(solve(prob_solownneqn,TRBDF2(),p=θ, abstol=1e-4, reltol=1e-4, saveat = nntsteps))
    end

    losses=[]
    
    function loss(θ)
        pred = predicts(θ)
        kloss=sum(abs,(pred[1,:].-kdata))./ sum(pred[1,:].+ kdata)
        yloss=sum(abs, (pred[2,:].-ydata))./sum(pred[2,:].+ydata)
        eloss=sum(abs,(pred[3,:].-edata))./sum(pred[3,:].+edata)
        return ((kloss+eloss+yloss)), pred
    end      

    callback(θ,l,pred) = begin
            push!(losses, l)
            false
    end
    
    tick()
    res1= DiffEqFlux.sciml_train(loss, nnp, ADAM(0.001),cb=callback, maxiters=100)
    res1= DiffEqFlux.sciml_train(loss, res1.minimizer, BFGS(initial_stepnorm=0.000001/100),cb=callback, maxiters=100)
    timed = tok()
        println("timed", Float64(timed))
        if timed > 500
            println("Took too long", timed)
            pred = Array{Float64}(undef, 3, getfield(size(kdata), 1))
            return years_available, kdata, ydata, edata, res1.minimizer, pred, df8, df5, df7
        end    


    while ((mean(losses[end-100:end-50])>=(1.001*mean(losses[end-49:end]))) || std(losses[end-49:end]) >=0.001) && length(losses) <3000
        tick()
        res1= DiffEqFlux.sciml_train(loss, res1.minimizer, ADAM(0.0001),cb=callback, maxiters=200)
        try
            res1= DiffEqFlux.sciml_train(loss, res1.minimizer, BFGS(initial_stepnorm=0.000001/100),cb=callback, maxiters=100)
        catch e
            res1= DiffEqFlux.sciml_train(loss, res1.minimizer, ADAM(0.0001),cb=callback, maxiters=100)
        end
        res1= DiffEqFlux.sciml_train(loss, res1.minimizer, ADAM(0.00001),cb=callback, maxiters=100)
        try
            res1= DiffEqFlux.sciml_train(loss, res1.minimizer, BFGS(initial_stepnorm=0.000001/100),cb=callback, maxiters=100)
        catch e
            res1= DiffEqFlux.sciml_train(loss, res1.minimizer, ADAM(0.00001),cb=callback, maxiters=100)
        end
        timed = tok()
        println("timed", Float64(timed))
        if timed > 900
            println("Took too long", timed)
            pred = Array{Float64}(undef, 3, getfield(size(kdata), 1))
            return years_available, kdata, ydata, edata, res1.minimizer, pred, df8, df5, df7
        end

    end
        pred = solve(prob_solownneqn, TRBDF2(),p=res1.minimizer, abstol=1e-4, reltol=1e-4, saveat = nntsteps)
    return years_available, kdata, ydata, edata, res1.minimizer, pred, df8, df5, df7

    end

generate_parameters_and_predictions (generic function with 1 method)

In [10]:
 function plot_graph(nnpred,country,nntstepsfull,kdata,ydata,edata, paras_set)
    upscale = 1 #8x upscaling in resolution
    fntsm = Plots.font("sans-serif", pointsize=round(12.0*upscale))
    fntlg = Plots.font("sans-serif", pointsize=round(16.0*upscale))
    default(titlefont=fntlg, guidefont=fntlg, tickfont=fntsm, legendfont=fntsm)
    default(size=(550*upscale,400*upscale)) #Plot canvas size
    default(dpi=300)
    
#     fctime = collect(Int(floor(size(nntstepsfull,1)*0.8))+1:1:size(nntstepsfull,1)) 
# #             println(fctime)
#             println(nntstepsfull)
    plotkyenn12ic= scatter(xaxis=nntstepsfull,nnpred[1:2,:]',
        label=[L"k_{sol}" L"y_{sol}"],color=[:red :blue],legend=(0.102,0.955),
        markershape=[:circle :diamond],markersize=4,
        ylabel=L"k^c_t,y^t_c",right_margin = 15Plots.mm)
            
    plot!(plotkyenn12ic,[kdata,ydata],label=[L"k_{data}" L"y_{data}"],linestyle=[:solid :dash],
        color=[:red :blue],ylim=(0,1.5.*round(maximum(kdata);sigdigits=1)),foreground_color_legend = nothing)

#     scatter!(plotkyenn12ic,nntstepsfull,nnpred[1:2,:]',
#         color=[:red :blue],markershape=[:circle :diamond], markersize=4,label=nothing)

    pr = twinx()
    
#     scatter!(pr,nntstepsfull,nnpred[3,:],
#         color=:green,legend=(0.89,0.954), markershape = [:utriangle], markersize=4, label=nothing)

    scatter!(pr,nntstepsfull,nnpred[3,:],
        label=L"e_{sol}",color=:green,legend=(0.89,0.954), markershape = [:utriangle], markersize=4,
        ylabel=L"e^t_c",right_margin = 15Plots.mm,
        foreground_color_legend = nothing,background_color_legend = nothing)
            
    plot!(pr,edata,label=L"e_{data}",color=:green,ylim=(0,1.5.*round(maximum(edata);sigdigits=1)),
                linestyle=:dot)
    
 xpts = collect(0:5:5*ceil(length(nntstepsfull)/5))
#     if xpts[end] != length(nntsteps)
#         push!(xpts,length(nntsteps))
        xpts[1]=1
#     end
    
   plot(plotkyenn12ic,xlabel = "years",xticks=xpts,box=:on,linewidth=2*upscale)
#     display(StatsPlots.plot(pl,xlabel = "Days post 21 March 2020",xticks=0:10:110,tickfont=12,
#         guidefont = 16,legendfontsize=12,legend=(0.1,0.92),
#         dpi=300,box=:on,linewidth=2*upscale))

    savefig(string(@__DIR__,"/new_plots_for_all_countries/model3_",country,"_", paras_set))
end


plot_graph (generic function with 1 method)

In [11]:
function calculate_metrics(best_model,kdata, ydata, edata)
    Botswana_k_pred = convert(Array{Float64},best_model[1,:])
    Botswana_y_pred = convert(Array{Float64},best_model[2,:])
    Botswana_e_pred = convert(Array{Float64},best_model[3,:])

    metrics = Float64[]
    push!(metrics,sqL2dist(Botswana_k_pred, identity.(kdata))/length(kdata))
    push!(metrics,sqL2dist(Botswana_y_pred, identity.(ydata))/length(ydata)) 
    push!(metrics,sqL2dist(Botswana_e_pred, identity.(edata))/length(edata))
    push!(metrics,L2dist(Botswana_k_pred, identity.(kdata))/length(kdata))
    push!(metrics,L2dist(Botswana_y_pred, identity.(ydata))/length(ydata))
    push!(metrics,L2dist(Botswana_e_pred, identity.(edata))/length(edata))
    push!(metrics,L1dist(convert(Array{Float64},Botswana_k_pred),identity.(kdata))/length(kdata))
    push!(metrics,L1dist(convert(Array{Float64},Botswana_y_pred),identity.(ydata))/length(ydata))
    push!(metrics,L1dist(convert(Array{Float64},Botswana_e_pred),identity.(edata))/length(edata))

    function r2_impl(data,pred)
    tss = sum((data .-mean(data)).^2)
    rss = sum((data .-pred).^2)
    r2 = 1- rss/tss
    return r2  
    end

    push!(metrics,r2_impl(kdata, Botswana_k_pred))
    push!(metrics,r2_impl(ydata, Botswana_y_pred))
    push!(metrics,r2_impl(edata, Botswana_e_pred))

    function Ar2_impl(data,pred, p)
    tss = sum((data .-mean(data)).^2)
    rss = sum((data .-pred).^2)
    r2 = 1- rss/tss
    n = size(data)[1]
    ar2 = 1 - abs((1 - r2)*(n-1)/(n-p))
    return ar2  
    end

    push!(metrics,Ar2_impl(kdata, Botswana_k_pred, 4))
    push!(metrics,Ar2_impl(ydata, Botswana_y_pred, 4))
    push!(metrics,Ar2_impl(edata, Botswana_e_pred, 4))

    push!(metrics,mean((kdata.- Botswana_k_pred)./kdata)*100)
    push!(metrics,mean((ydata.- Botswana_y_pred)./ydata)*100)
    push!(metrics,mean((edata.- Botswana_e_pred)./edata)*100)

    push!(metrics,mean(abs.((kdata.- Botswana_k_pred)./kdata))*100)
    push!(metrics,mean(abs.((ydata.- Botswana_y_pred)./ydata))*100)
    push!(metrics,mean(abs.((edata.- Botswana_e_pred)./edata))*100)

    push!(metrics,mean(atan.(abs.((kdata.- Botswana_k_pred)./kdata)))*100)
    push!(metrics,mean(atan.(abs.((ydata.- Botswana_y_pred)./ydata)))*100)
    push!(metrics,mean(atan.(abs.((edata.- Botswana_e_pred)./edata)))*100)

    push!(metrics,mean(kdata.- Botswana_k_pred))
    push!(metrics,mean(ydata.- Botswana_y_pred))
    push!(metrics,mean(edata.- Botswana_e_pred))

    function loglikelihood_calc(data,pred)
    rss = sum((data .-pred).^2)
    n = length(pred)
    return -n/2*(log(2pi*rss/n)+1)
    end
    # implementation from julia: https://github.com/JuliaStats/GLM.jl/blob/950579166c52ff1cbbeab75cbc23235b30640802/src/lm.jl

    push!(metrics,loglikelihood_calc(kdata, Botswana_k_pred))
    push!(metrics,loglikelihood_calc(ydata, Botswana_y_pred))
    push!(metrics,loglikelihood_calc(edata, Botswana_e_pred))

    function aic_calc(data, pred, params)
        L = loglikelihood_calc(data,pred)
        return 2*params-2*L
    end

    push!(metrics,aic_calc(kdata, Botswana_k_pred, 5))
    push!(metrics,aic_calc(ydata, Botswana_y_pred, 5))
    push!(metrics,aic_calc(edata, Botswana_e_pred, 5))

    function aicc_calc(data, pred, params)
        n = length(pred)
        L = loglikelihood_calc(data,pred)
        return -2*L + 2*params + 2*params*(params+1)/(n-params-1)
    end


    push!(metrics,aicc_calc(kdata, Botswana_k_pred, 5))
    push!(metrics,aicc_calc(ydata, Botswana_y_pred, 5))
    push!(metrics,aicc_calc(edata, Botswana_e_pred, 5))

    function bic_calc(data, pred, params)
        n = length(pred)
        L = loglikelihood_calc(data,pred)
        return -2*L + params*log(n)
    end



    push!(metrics,bic_calc(kdata, Botswana_k_pred, 5))
    push!(metrics,bic_calc(ydata, Botswana_y_pred, 5))
    push!(metrics,bic_calc(edata, Botswana_e_pred, 5))

    return metrics
end


calculate_metrics (generic function with 1 method)

In [12]:
store_parameters_and_metrics = DataFrame(country = String[], 
    delta1 = Float64[],    gB1 = Float64[],    alpha1 = Float64[],    gA1 = Float64[],
    MSE1_kt = Float64[],    MSE1_yt = Float64[],    MSE1_et = Float64[],
    RMSE1_kt = Float64[],    RMSE1_yt = Float64[],    RMSE1_et = Float64[],
    MAE1_kt = Float64[],    MAE1_yt = Float64[],    MAE1_et = Float64[],
    Rsq1_kt = Float64[],    Rsq1_yt = Float64[],    Rsq1_et = Float64[],
    ARsq1_kt = Float64[],    ARsq1_yt = Float64[],    ARsq1_et = Float64[],
    MPE1_kt = Float64[],    MPE1_yt = Float64[],    MPE1_et = Float64[],
    MAPE1_kt = Float64[],    MAPE1_yt = Float64[],    MAPE1_et = Float64[],
    MAAPE1_kt = Float64[],    MAAPE1_yt = Float64[],    MAAPE1_et = Float64[],
    MBE1_kt = Float64[],    MBE1_yt = Float64[],    MBE1_et = Float64[],
    loglik1_kt = Float64[],    loglik1_yt = Float64[],    loglik1_et = Float64[],
    aic1_kt = Float64[],    aic1_yt = Float64[],    aic1_et = Float64[],
    aicc1_kt = Float64[],    aicc1_yt = Float64[],    aicc1_et = Float64[],
    bic1_kt = Float64[],    bic1_yt = Float64[],    bic1_et = Float64[],
    delta2 = Float64[],    gB2 = Float64[],    alpha2 = Float64[],    gA2 = Float64[],
    MSE2_kt = Float64[],    MSE2_yt = Float64[],    MSE2_et = Float64[],
    RMSE2_kt = Float64[],    RMSE2_yt = Float64[],    RMSE2_et = Float64[],
    MAE2_kt = Float64[],    MAE2_yt = Float64[],    MAE2_et = Float64[],
    Rsq2_kt = Float64[],    Rsq2_yt = Float64[],    Rsq2_et = Float64[],
    ARsq2_kt = Float64[],    ARsq2_yt = Float64[],    ARsq2_et = Float64[],
    MPE2_kt = Float64[],    MPE2_yt = Float64[],    MPE2_et = Float64[],
    MAPE2_kt = Float64[],    MAPE2_yt = Float64[],    MAPE2_et = Float64[],
    MAAPE2_kt = Float64[],    MAAPE2_yt = Float64[],    MAAPE2_et = Float64[],
    MBE2_kt = Float64[],    MBE2_yt = Float64[],    MBE2_et = Float64[],
    loglik2_kt = Float64[],    loglik2_yt = Float64[],    loglik2_et = Float64[],
    aic2_kt = Float64[],    aic2_yt = Float64[],    aic2_et = Float64[],
    aicc2_kt = Float64[],    aicc2_yt = Float64[],    aicc2_et = Float64[],
    bic2_kt = Float64[],    bic2_yt = Float64[],    bic2_et = Float64[]
   )

CSV.write(string(@__DIR__,"/parameters_and_metrics.csv"), store_parameters_and_metrics)


"/home/ziyu/solow/NODE/Neural Ordinary Differential Equations for the Regression and Prediction of Macroeconomics Data under the Green Solow Model/Model 3/Kang Hao/parameters_and_metrics.csv"

In [13]:
store_parameters_and_differentiation_metrics = DataFrame(country = String[], 
    delta1 = Float64[],    gB1 = Float64[],    alpha1 = Float64[],    gA1 = Float64[],
    MSE1_kt = Float64[],    MSE1_yt = Float64[],    MSE1_et = Float64[],
    RMSE1_kt = Float64[],    RMSE1_yt = Float64[],    RMSE1_et = Float64[],
    MAE1_kt = Float64[],    MAE1_yt = Float64[],    MAE1_et = Float64[],
    Rsq1_kt = Float64[],    Rsq1_yt = Float64[],    Rsq1_et = Float64[],
    ARsq1_kt = Float64[],    ARsq1_yt = Float64[],    ARsq1_et = Float64[],
    MPE1_kt = Float64[],    MPE1_yt = Float64[],    MPE1_et = Float64[],
    MAPE1_kt = Float64[],    MAPE1_yt = Float64[],    MAPE1_et = Float64[],
    MAAPE1_kt = Float64[],    MAAPE1_yt = Float64[],    MAAPE1_et = Float64[],
    MBE1_kt = Float64[],    MBE1_yt = Float64[],    MBE1_et = Float64[],
    loglik1_kt = Float64[],    loglik1_yt = Float64[],    loglik1_et = Float64[],
    aic1_kt = Float64[],    aic1_yt = Float64[],    aic1_et = Float64[],
    aicc1_kt = Float64[],    aicc1_yt = Float64[],    aicc1_et = Float64[],
    bic1_kt = Float64[],    bic1_yt = Float64[],    bic1_et = Float64[],
    delta2 = Float64[],    gB2 = Float64[],    alpha2 = Float64[],    gA2 = Float64[],
    MSE2_kt = Float64[],    MSE2_yt = Float64[],    MSE2_et = Float64[],
    RMSE2_kt = Float64[],    RMSE2_yt = Float64[],    RMSE2_et = Float64[],
    MAE2_kt = Float64[],    MAE2_yt = Float64[],    MAE2_et = Float64[],
    Rsq2_kt = Float64[],    Rsq2_yt = Float64[],    Rsq2_et = Float64[],
    ARsq2_kt = Float64[],    ARsq2_yt = Float64[],    ARsq2_et = Float64[],
    MPE2_kt = Float64[],    MPE2_yt = Float64[],    MPE2_et = Float64[],
    MAPE2_kt = Float64[],    MAPE2_yt = Float64[],    MAPE2_et = Float64[],
    MAAPE2_kt = Float64[],    MAAPE2_yt = Float64[],    MAAPE2_et = Float64[],
    MBE2_kt = Float64[],    MBE2_yt = Float64[],    MBE2_et = Float64[],
    loglik2_kt = Float64[],    loglik2_yt = Float64[],    loglik2_et = Float64[],
    aic2_kt = Float64[],    aic2_yt = Float64[],    aic2_et = Float64[],
    aicc2_kt = Float64[],    aicc2_yt = Float64[],    aicc2_et = Float64[],
    bic2_kt = Float64[],    bic2_yt = Float64[],    bic2_et = Float64[]
   )

CSV.write(string(@__DIR__,"/diff_parameters_and_metrics.csv"), store_parameters_and_differentiation_metrics)

"/home/ziyu/solow/NODE/Neural Ordinary Differential Equations for the Regression and Prediction of Macroeconomics Data under the Green Solow Model/Model 3/Kang Hao/diff_parameters_and_metrics.csv"

In [14]:
for i in country_list
    try
    println("Loading parameters for country: ", i)
    all_parameters = get_parameters(i)
    set1 = all_parameters[1][:]
    set2 = all_parameters[2:5]
    println("Training parameters for country: ", i)
    years_available1, kdata1, ydata1, edata1, params1, pred1, df8, df5, df7 = 
        generate_parameters_and_predictions(set1[1], set1[2], set1[3], set1[4], i)
    _, kdata2, ydata2, edata2, params2, pred2, _, _, _ =
        generate_parameters_and_predictions(set2[1][1], set2[2][1], set2[3][1], set2[4][1], i)
    timesteps = range(1.0e0, years_available1*1.0, length=years_available1)
    println("Plotting graphs for country: ", i)
    plot_graph(pred1,i,timesteps,kdata1,ydata1,edata1, "set1")
    plot_graph(pred2,i,timesteps,kdata2,ydata2,edata2, "set2")
    println("Updating csv for parameters for country: ", i)
    push!(store_parameters_and_metrics, (vcat([i], 
            set1, 
            calculate_metrics(pred1, kdata1, ydata1, edata1), 
            set2[1], 
            set2[2], 
            set2[3], 
            set2[4], 
            calculate_metrics(pred2, kdata2, ydata2, edata2))))
    println(store_parameters_and_metrics)
    println("Updating csv for differentiation parameters for country: ", i)
    pred1_k = convert(Array{Float64},pred1[1,:])
    pred1_y = convert(Array{Float64},pred1[2,:])
    pred1_e = convert(Array{Float64},pred1[3,:])
    pred2_k = convert(Array{Float64},pred2[1,:])
    pred2_y = convert(Array{Float64},pred2[2,:])
    pred2_e = convert(Array{Float64},pred2[3,:])
    dk1 = pred1_k[2:end] .- pred1_k[1:end-1]
    dy1 = pred1_y[2:end] .- pred1_y[1:end-1]
    de1 = pred1_e[2:end] .- pred1_e[1:end-1]
    dk2 = pred2_k[2:end] .- pred2_k[1:end-1]
    dy2 = pred2_y[2:end] .- pred2_y[1:end-1]
    de2 = pred2_e[2:end] .- pred2_e[1:end-1]
    dpred1 = transpose(hcat(dk2, dy2, de2))
    dpred2 = transpose(hcat(dk2, dy2, de2))
    dkdata = identity.(df5[51-years_available1:end])
    dydata = identity.(df7[51-years_available1:end])
    dedata = identity.(df8[51-years_available1:end])
    push!(store_parameters_and_differentiation_metrics, (vcat([i], 
            set1, 
            calculate_metrics(dpred1, dkdata, dydata, dedata), 
            set2[1], 
            set2[2], 
            set2[3], 
            set2[4], 
            calculate_metrics(dpred2, dkdata, dydata, dedata))))
    CSV.write("parameters_and_metrics.csv", store_parameters_and_metrics)
    CSV.write("differentiation_parameters_and_metrics.csv", store_parameters_and_differentiation_metrics)
    catch e
        println("Error with country ", i, ": ", e)
    end
end

Loading parameters for country: Albania
Training parameters for country: Albania
parameters received: 0.045063099706593286, 0.00470056070832222, 0.013959044973194171, 0.052363804501125814


┌ Info:  started timer at: 2021-04-02T15:46:45.12
└ @ TickTock /home/ziyu/.julia/packages/TickTock/RsTHR/src/TickTock.jl:32
loss: 0.272: 100%|██████████████████████████████████████| Time: 0:00:02


timed86.397986203


┌ Info:  started timer at: 2021-04-02T15:48:11.532
└ @ TickTock /home/ziyu/.julia/packages/TickTock/RsTHR/src/TickTock.jl:32
loss: 0.272: 100%|██████████████████████████████████████| Time: 0:00:02
loss: 0.271: 100%|██████████████████████████████████████| Time: 0:00:01


timed7.314676221
parameters received: 0.02516925114441621, 0.1499509228194447, -0.03333882116460529, -0.03353785281089472


...

timed5.368596852


┌ Info:  started timer at: 2021-04-02T20:12:29.159
└ @ TickTock /home/ziyu/.julia/packages/TickTock/RsTHR/src/TickTock.jl:32
loss: 0.159: 100%|██████████████████████████████████████| Time: 0:00:05
loss: 0.159: 100%|██████████████████████████████████████| Time: 0:00:02


timed15.324056653
Plotting graphs for country: Uruguay
Updating csv for parameters for country: Uruguay
63×87 DataFrame
 Row │ country      delta1       gB1           alpha1        gA1           MSE1_kt      MSE1_yt      MSE1_et       RMSE1_kt     RMSE1_yt     RMSE1_et     MAE1_kt      MAE1_yt      MAE1_et     Rsq1_kt     Rsq1_yt       Rsq1_et     ARsq1_kt     ARsq1_yt    ARsq1_et    MPE1_kt      MPE1_yt      MPE1_et     MAPE1_kt   MAPE1_yt  MAPE1_et  MAAPE1_kt  MAAPE1_yt  MAAPE1_et  MBE1_kt       MBE1_yt       MBE1_et       loglik1_kt  loglik1_yt  loglik1_et  aic1_kt   aic1_yt   aic1_et      aicc1_kt   aicc1_yt  aicc1_et    bic1_kt    bic1_yt   bic1_et      delta2     gB2          alpha2        gA2          MSE2_kt        MSE2_yt        MSE2_et        RMSE2_kt       RMSE2_yt       RMSE2_et       MAE2_kt      MAE2_yt      MAE2_et       Rsq2_kt        Rsq2_yt        Rsq2_et       ARsq2_kt       ARsq2_yt      ARsq2_et       MPE2_kt         MPE2_yt        MPE2_et        MAPE2_kt       MAP

  53 │ Singapore     0.0820707   -0.0390992     0.0416231     0.0400437    0.000163746  1.4647e-6    10.3028       0.00210371   0.000198963  0.527688     0.00947987   0.000983659  2.31591      0.943922    0.968252     -0.273029    0.938823     0.965365   -0.388759     -2.15357     4.73271     -9.94051    12.1635    6.41846  25.713     12.0461     6.40097   21.3191   -0.00124022    0.000573916  -0.0306444      108.767      196.026  -95.6505    -207.535  -382.051   201.301     -205.599   -380.116   203.236    -199.48    -373.997   209.356     1.5723      0.0643983    0.0815765    -0.0397824   Inf            Inf            Inf            Inf            Inf            Inf            2.07249e290  2.75191e275   3.05602e275  -Inf           -Inf           -Inf          -Inf           -Inf          -Inf             -1.20482e293   -2.34344e279   -2.38479e276    1.20482e293    2.34344e279    2.38479e276  142.521    129.485    118.871    -2.07249e290  -2.75191e275  -3.05602e275  -Inf          -Inf

Updating csv for differentiation parameters for country: Uruguay
